In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
ls

basic_prediction.ipynb  data/  DSL_statement_generation.ipynb  ra_tasks.md  scripts/


In [ ]:
from transformers import (
    AutoTokenizer,
    AutoModelForSequenceClassification
)

import numpy as np
import pandas as pd
import torch
from sklearn.feature_extraction.text import TfidfVectorizer
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, TensorDataset
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from transformers import BertTokenizer, BertModel
from torch.utils.data import DataLoader, Dataset
from sklearn.metrics import f1_score, accuracy_score


### Surrogate Q

In [ ]:
!pip install openai

In [ ]:
import os
import numpy as np
import pandas as pd
import time
from openai import OpenAI
from getpass import getpass
import base64
import requests
import random

openai_api_key = 'YOURKEY'
os.environ["OPENAI_API_KEY"] = openai_api_key

client = OpenAI()
image_directory = './phone_screenshots'

def encode_image(image_path):
    with open(image_path, "rb") as image_file:
        return base64.b64encode(image_file.read()).decode('utf-8')

headers = {
    "Content-Type": "application/json",
    "Authorization": f"Bearer {os.getenv('OPENAI_API_KEY')}"
}

In [ ]:
data = pd.read_csv('data/Statement corpus.csv')

In [ ]:
data

statement  behavior  everyday  \
0                                         1 plus 1 is 2         0         1   
1                               5 is alot bigger than 1         0         0   
2     a balanced diet and regular exercise is needed...         1         1   
3                                       a ball is round         0         1   
4          a baton twirler doesn't want a broken finger         0         1   
...                                                 ...       ...       ...   
4402  young people should not believe that they cann...         0         0   
4403      your credibility is the currency of the realm         1         0   
4404    your religion is not the only one true religion         1         1   
4405            zero plus any number equals that number         1         0   
4406  zest is the secret of all beauty there is no b...         0         0   

      figure_of_speech  judgment  opinion  reasoning  \
0                    0         0        0          1   
1                    0         0        0          0   
2                    0         1        0          1   
3                    0         0        0          0   
4                    0         1        1          0   
...                ...       ...      ...        ...   
4402                 0         0        0          0   
4403                 1         0        0          1   
4404                 0         1        1          1   
4405                 1         0        1          0   
4406                 1         1        0          0   

                           category        elicitation  
0             Mathematics and logic  category response  
1             Mathematics and logic  category response  
2                Health and fitness  category response  
3     Natural and physical sciences        Concept Net  
4                  Human activities        Concept Net  
...                             ...                ...  
4402             History and events         news media  
4403                People and self           aphorism  
4404    Religion and belief systems  category response  
4405              General reference  category response  
4406              General reference           aphorism  

[4407 rows x 9 columns]

In [ ]:
description = '''
For each statement provided below, please classify it into binary categories for the following labels. For each label, return strictly only '1' for a match and only '0' otherwise, following the detailed descriptions provided:

Behavior:
Social (1): Relates to beliefs, perceptions, preferences, and socially constructed rules governing human experience, either "real" or opinion-based and of human origins. Example: 'I exist and am the same person I was yesterday.'
Physical (0): Pertains to objective features of the world, governed by natural laws like physics or biology, and can be measured or logically derived. Example: 'The Earth is the third planet from the Sun.'

Everyday:
Everyday (1): Situations commonly encountered or potentially encountered in ordinary life. Example: 'Touching a hot stove will burn you.'
Abstract (0): Regularities or conclusions not directly observable or derived solely from personal experience. Example: 'Capitalism is a better economic system than Communism.'

Figure of Speech:
Figure of speech (1): Contains aphorisms, metaphors, or hyperboles. Example: 'Birds of a feather flock together.'
Literal language (0): Plain and direct language that means exactly what it says. Example: 'The sky is blue.'

Judgment:
Normative (1): Involves a judgment, belief, value, or social norm. Example: 'Treat others how you want them to treat you.'
Positive (0): Refers to empirical regularities or scientific laws. Example: 'The sun rises in the east and sets in the west.'

Opinion:
Opinion (1): Subjective statements that might be believed true but cannot be objectively proven. Example: 'FDR was the greatest US president of the 20th Century.'
Factual (0): Statements that can be independently verified as correct or incorrect. Example: 'Obama was the 24th president of the United States (this is incorrect).'

Reasoning:
Knowledge (1): Observations about the world, true or false, subjective or objective. Example: 'Dogs are nicer than cats.'
Reasoning (0): Conclusions derived from combining knowledge and logic. Example: 'My dog is wagging its tail, therefore it is happy.'

The output should be in JSON schema.

Please classify the following statement:
'''

# For example, your return should follow the JSON schema like this:
# {
#   Behavior: 0,
#   Everyday: 0,
#   Figure of Speech: 0,
#   Judgment: 0,
#   Opinion: 0,
#   Reasoning: 0
# }

In [ ]:
def generateQ(description, question):
    response = client.chat.completions.create(
        model="gpt-4-turbo-preview",
        response_format={ "type": "json_object" },
        messages=[
            {"role": "system", "content": description},
            {
            "role": "user",
            "content": [
                {"type": "text", "text": question},
            ],
        }
        ],
        logprobs=True,
        top_logprobs=1,
        )
    return response

In [ ]:
import re

def extract_class(line):
    return re.findall(r'"(.*?)"', line)

def extract_digit(line):
    match = re.search(r'[01]', line)
    if match:
        return match.group()
    else:
        return None

def parse_response(statement, msg):
    lines = msg.strip().split('\n')
    result_dict = {}
    result_dict['statement'] = statement
    for line in lines:
        if ': ' in line:
            label, value = line.split(': ')
            value = extract_digit(value)[0]
            label = extract_class(label)[0]
            print(label, value)
            result_dict[label] = int(value)
    return result_dict

In [ ]:
outputs = []

In [ ]:
for index, row in data.iterrows():
    if index < 4000:
        continue
    # if index == 4000:
    #     break
    question = row['statement']
    response = generateQ(description, question)
    msg = response.choices[0].message.content
    print(question)
    response_data = parse_response(question, msg)
    outputs.append(response_data)

we should enact policies which are fiscally responsible
Behavior 1
Everyday 0
Figure of Speech 0
Judgment 1
Opinion 1
Reasoning 0
we should ensure leadership and strength back to congress
Behavior 1
Everyday 0
Figure of Speech 0
Judgment 1
Opinion 1
Reasoning 0
we should ensure police have body cameras on them
Behavior 1
Everyday 0
Figure of Speech 0
Judgment 1
Opinion 1
Reasoning 0
we should fight for conservative solutions
Behavior 1
Everyday 0
Figure of Speech 0
Judgment 1
Opinion 1
Reasoning 0
we should fight for health care coverage
Behavior 1
Everyday 0
Figure of Speech 0
Judgment 1
Opinion 1
Reasoning 0
we should fight for the green new deal
Behavior 1
Everyday 0
Figure of Speech 0
Judgment 1
Opinion 1
Reasoning 0
we should fight the imperative to take things personally when speaking to others
Behavior 1
Everyday 0
Figure of Speech 0
Judgment 1
Opinion 1
Reasoning 0
we should fight to stop spread of covid19
Behavior 1
Everyday 1
Figure of Speech 0
Judgment 1
Opinion 1
Reasoning 

In [ ]:
Q = pd.DataFrame(outputs)
Q.to_csv("Q3.csv", index=False)
Q

statement  Behavior  Everyday  \
0     remaining hydrated is important since your bod...         0         1   
1     remember democracy never lasts long it soon wa...         0         0   
2     remember that life is neither pain nor pleasur...         1         0   
3     remember that there is nothing stable in human...         0         0   
4     remember this is your body your residence for ...         1         1   
...                                                 ...       ...       ...   
1402  young people should not believe that they cann...         0         1   
1403      your credibility is the currency of the realm         1         0   
1404    your religion is not the only one true religion         1         0   
1405            zero plus any number equals that number         0         0   
1406  zest is the secret of all beauty there is no b...         1         0   

      Figure of Speech  Judgment  Opinion  Reasoning  Judgement  
0                    0       1.0        0          1        NaN  
1                    1       1.0        1          0        NaN  
2                    0       1.0        1          0        NaN  
3                    1       1.0        1          0        NaN  
4                    1       1.0        1          0        NaN  
...                ...       ...      ...        ...        ...  
1402                 0       1.0        1          0        NaN  
1403                 1       1.0        1          0        NaN  
1404                 0       1.0        1          0        NaN  
1405                 0       0.0        0          0        NaN  
1406                 1       1.0        1          0        NaN  

[1407 rows x 8 columns]

In [ ]:
Q.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1407 entries, 0 to 1406
Data columns (total 8 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   statement         1407 non-null   object 
 1   Behavior          1407 non-null   int64  
 2   Everyday          1407 non-null   int64  
 3   Figure of Speech  1407 non-null   int64  
 4   Judgment          1406 non-null   float64
 5   Opinion           1407 non-null   int64  
 6   Reasoning         1407 non-null   int64  
 7   Judgement         1 non-null      float64
dtypes: float64(2), int64(5), object(1)
memory usage: 88.1+ KB


In [ ]:
ls

basic_prediction.ipynb  data/  DSL_statement_generation.ipynb  ra_tasks.md  scripts/


In [ ]:
Q

[{'statement': '1 plus 1 is 2',
  'Behavior': 0,
  'Everyday': 0,
  'Figure of Speech': 0,
  'Judgment': 0,
  'Opinion': 0,
  'Reasoning': 0}]

### Preprocessing Q

In [ ]:
Q1 = pd.read_csv("Q.csv")
Q2 = pd.read_csv("Q_second.csv")
Q3 = pd.read_csv("Q3.csv")

In [ ]:
def fixQ(df, filePath=None):
    if 'Judgement' in df.columns:
        df['Judgment'] = df['Judgement'].where(df['Judgement'].notna(), df['Judgment'])
        df.drop('Judgement', axis=1, inplace=True)
    for col in df.select_dtypes(include='number').columns:
        df[col] = df[col].astype(int)
    if  filePath:
        df.to_csv(filePath, index=False)
    df.head()
    return df

Q1 = fixQ(Q1)
Q2 = fixQ(Q2)
Q3 = fixQ(Q3)

In [ ]:
mergeQ = pd.concat([Q1, Q2, Q3])
mergeQ = mergeQ.reset_index(drop=True)
mergeQ.to_csv("data/mergeQ.csv")

In [ ]:
mergeQ.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4407 entries, 0 to 4406
Data columns (total 7 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   statement         4407 non-null   object
 1   Behavior          4407 non-null   int64 
 2   Everyday          4407 non-null   int64 
 3   Figure of Speech  4407 non-null   int64 
 4   Judgment          4407 non-null   int64 
 5   Opinion           4407 non-null   int64 
 6   Reasoning         4407 non-null   int64 
dtypes: int64(6), object(1)
memory usage: 241.1+ KB


### Step1: Train g(Q,X) supervised model

In [ ]:
mergeQ = pd.read_csv("data/mergeQ.csv")
mergeQ = mergeQ.iloc[:,1:]

In [ ]:
token_feature = 1000
vectorizer = TfidfVectorizer(max_features=token_feature)
tfidf_features = vectorizer.fit_transform(data['statement'])
X_features = torch.tensor(tfidf_features.toarray(), dtype=torch.float32)
tensor_X = pd.DataFrame(X_features.numpy())

X_combined = pd.concat([mergeQ, tensor_X], axis=1)
Y = torch.tensor(data[['behavior', 'everyday', 'figure_of_speech', 'judgment', 'opinion', 'reasoning']].values, dtype=torch.float32)

In [ ]:
mergeQ.head()

statement  Behavior  Everyday  \
0                                      1 plus 1 is 2         0         1   
1                            5 is alot bigger than 1         0         0   
2  a balanced diet and regular exercise is needed...         0         1   
3                                    a ball is round         0         1   
4       a baton twirler doesn't want a broken finger         1         1   

   Figure of Speech  Judgment  Opinion  Reasoning  
0                 0         0        0          1  
1                 1         0        0          0  
2                 0         1        0          0  
3                 0         0        0          1  
4                 0         0        1          1

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(mergeQ, Y, test_size=0.2, random_state=42)

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
def tokenize_data(text):
    return tokenizer(text, padding='max_length', max_length=512, truncation=True, return_tensors="pt")

X_train_tokens = [tokenize_data(text) for text in X_train['statement']]
X_test_tokens = [tokenize_data(text) for text in X_test['statement']]

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


In [ ]:
class TextNN(nn.Module):
    def __init__(self):
        super().__init__()
        self.bert = BertModel.from_pretrained('bert-base-uncased')
        self.classifier = nn.Linear(self.bert.config.hidden_size + 6, 6)

    def forward(self, input_ids, attention_mask, features):
        outputs = self.bert(input_ids=input_ids, attention_mask=attention_mask)
        pooled_output = outputs.pooler_output
        combined_features = torch.cat((pooled_output, features), dim=1)
        # print("Shape of combined features:", combined_features.shape)
        logits = self.classifier(combined_features)
        return logits

In [ ]:
# class TextAndTabularDataset(Dataset):
#     def __init__(self, texts, features, labels, tokenizer, max_length=512):
#         self.texts = texts
#         self.features = features
#         self.labels = labels
#         self.tokenizer = tokenizer
#         self.max_length = max_length

#     def __len__(self):
#         return len(self.texts)

#     def __getitem__(self, idx):
#         text_data = self.tokenizer(self.texts[idx],
#                                    padding='max_length',
#                                    max_length=self.max_length,
#                                    truncation=True,
#                                    return_tensors="pt")
#         input_ids = text_data['input_ids'].squeeze(0)  # Removing batch dimension
#         attention_mask = text_data['attention_mask'].squeeze(0)

#         features = torch.tensor(self.features[idx], dtype=torch.float32)
#         labels = torch.tensor(self.labels[idx], dtype=torch.float32)

#         return input_ids, attention_mask, features, labels

In [ ]:
X_train

statement  Behavior  Everyday  \
4336  you think more clearly after a good night's sleep         0         1   
3505  the last thing you do when you take a bath is ...         0         1   
3134  something that might happen while getting a go...         0         1   
1448  if john pulls mary away mary will assume she i...         1         1   
1749        if max accepts the job then sam feels proud         1         1   
...                                                 ...       ...       ...   
3444            the higher you go the cooler it becomes         0         0   
466   during economic crisis local businesses should...         1         0   
3092  something that might happen as a consequence o...         0         1   
3772   waiting for luck is similar to waiting for death         0         0   
860   if alex calls sam's mother they would have a c...         0         1   

      Figure of Speech  Judgment  Opinion  Reasoning  
4336                 0         0        1          0  
3505                 0         0        0          1  
3134                 0         0        0          1  
1448                 0         1        1          0  
1749                 0         1        1          0  
...                ...       ...      ...        ...  
3444                 0         0        0          1  
466                  0         1        1          0  
3092                 0         0        0          1  
3772                 1         1        1          0  
860                  0         0        0          1  

[3525 rows x 7 columns]

In [ ]:
class TokenDataset(Dataset):
    def __init__(self, tokens, features, labels):
        self.tokens = tokens
        self.features = features
        self.labels = labels

    def __len__(self):
        return len(self.labels)

    def __getitem__(self, idx):
        input_ids = self.tokens[idx]['input_ids'].squeeze(0)
        attention_mask = self.tokens[idx]['attention_mask'].squeeze(0)
        features = self.features[idx]
        label = self.labels[idx]
        # print(input_ids.shape, attention_mask.shape, features.shape)
        return input_ids, attention_mask, features, label

In [ ]:
train_features = torch.tensor(X_train.drop('statement', axis=1).values, dtype=torch.float32)
test_features = torch.tensor(X_test.drop('statement', axis=1).values, dtype=torch.float32)
train_labels = y_train
test_labels = y_test

train_dataset = TokenDataset(X_train_tokens, train_features, train_labels)
test_dataset = TokenDataset(X_test_tokens, test_features, test_labels)

train_loader = DataLoader(train_dataset, batch_size=16, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=16, shuffle=False)

In [ ]:
##
for input_ids, attention_mask, features, labels in train_loader:
    print()

In [ ]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f'current device: {device}')
model = TextNN().to(device)

current device: cuda


In [ ]:
model.load_state_dict(torch.load('model.pth'))

In [ ]:
def evaluate(model, data_loader, criterion, device):
    model.eval()
    total_loss = 0
    all_labels = []
    all_predictions = []

    with torch.no_grad():
        for input_ids, attention_mask, features, labels in data_loader:
            input_ids = input_ids.to(device)
            attention_mask = attention_mask.to(device)
            features = features.to(device)
            labels = labels.to(device)

            outputs = model(input_ids, attention_mask, features)
            loss = criterion(outputs, labels)
            total_loss += loss.item()
            predictions = torch.sigmoid(outputs).round()

            all_labels.extend(labels.cpu().numpy())
            all_predictions.extend(predictions.detach().cpu().numpy())

    average_loss = total_loss / len(data_loader)
    accuracy = accuracy_score(all_labels, all_predictions)
    macrof1 = f1_score(all_labels, all_predictions, average='macro')
    microf1 = f1_score(all_labels, all_predictions, average='micro')
    return average_loss, accuracy, macrof1, microf1

In [ ]:
optimizer = torch.optim.Adam(model.parameters(), lr=1e-4)
criterion = nn.BCEWithLogitsLoss()
epoch = 5

for epoch in range(epoch):
    model.train()
    total_loss = 0
    all_labels = []
    all_predictions = []
    flag = 0
    for input_ids, attention_mask, features, labels in train_loader:
        # if flag==5:
        #     break
        optimizer.zero_grad()
        logits = model(input_ids.to(device),
                       attention_mask.to(device),
                       features.to(device))
        loss = criterion(logits, labels.to(device))
        loss.backward()
        optimizer.step()

        total_loss += loss.item()
        predictions = torch.sigmoid(logits).round()

        all_labels.extend(labels.cpu().numpy())
        all_predictions.extend(predictions.detach().cpu().numpy())
        flag += 1

    average_loss = total_loss / len(train_loader)
    accuracy = accuracy_score(all_labels, all_predictions)
    macrof1 = f1_score(all_labels, all_predictions, average='macro')
    microf1 = f1_score(all_labels, all_predictions, average='micro')
    print(f'epoch {epoch} === Training loss: {average_loss:.4f}, Accuracy: {accuracy:.4f}, Macro F1 : {macrof1:.4f}, Micro F1 : {microf1:.4f} ===')

    test_loss, test_accuracy, macrof1, microf1 = evaluate(model, test_loader, criterion, device)
    print(f'=== Test loss: {test_loss:.4f}, Accuracy: {test_accuracy:.4f},  Macro F1 : {macrof1:.4f}, Micro F1 : {microf1:.4f} ===')

Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])


In [ ]:
torch.save(model.state_dict(), 'model0+10.pth')

In [ ]:
test_loss, test_accuracy, macrof1, microf1 = evaluate(model, test_loader, criterion, device)
print(f'=== Test loss: {test_loss:.4f}, Accuracy: {test_accuracy:.4f},  Macro F1 : {macrof1:.4f}, Micro F1 : {microf1:.4f} ===')

Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])


In [ ]:
labels_array = y_test.cpu().numpy()
predictions_gpt = X_test.iloc[:, -6:].values

accuracy_gpt = accuracy_score(labels_array, predictions_gpt)
macrof1_gpt = f1_score(labels_array, predictions_gpt, average='macro')
microf1_gpt = f1_score(labels_array, predictions_gpt, average='micro')
print(f'Surrogate Estimation: === Accuracy: {accuracy_gpt:.4f},  Macro F1 : {macrof1_gpt:.4f}, Micro F1 : {microf1_gpt:.4f} ===')

GPT Evaluation: === Accuracy: 0.0998,  Macro F1 : 0.6191, Micro F1 : 0.6436 ===


#### Save

In [56]:
l

basic_prediction.ipynb  data/  DSL.ipynb  models/  ra_tasks.md  scripts/


In [59]:
from transformers import BertModel, BertConfig, PreTrainedModel
import torch
import torch.nn as nn

class TransTextNN(PreTrainedModel):
    def __init__(self):
        super().__init__(BertConfig.from_pretrained("bert-base-uncased"))
        self.bert = BertModel.from_pretrained("bert-base-uncased")
        self.classifier = nn.Linear(self.config.hidden_size + 6, 6)

    def forward(self, input_ids, attention_mask, features):
        outputs = self.bert(input_ids=input_ids, attention_mask=attention_mask)
        pooled_output = outputs.pooler_output
        combined_features = torch.cat((pooled_output, features), dim=1)
        logits = self.classifier(combined_features)
        return logits

state_dict = torch.load("models/model0+5.pth")
model = TransTextNN.from_pretrained("models")
model.load_state_dict(state_dict)
model.save_pretrained("huggingface_model")

AttributeError: 'NoneType' object has no attribute 'from_pretrained'

### Step2: Construct Bias-Corrected Pseudo-Outcomes

In [ ]:
def pseudo_construction(model, X_text, R=0):
    model.eval()
    total_samples = len(test_loader.dataset)
    labeled_samples = sum(1 for _, _, _, label in test_loader.dataset if label is not None)
    pi_Q_X = labeled_samples / total_samples

    pseudo_outcomes = []
    actual_labels = []
    mask_collected = []

    with torch.no_grad():
        for input_ids, attention_mask, features, label in test_loader:
            input_ids, attention_mask, features = input_ids.to(device), attention_mask.to(device), features.to(device)
            outputs = model(input_ids, attention_mask, features)
            predictions = torch.sigmoid(outputs).squeeze().cpu().numpy()
            R = 1 if label is not None else 0
            if R:
                actual_label = label.cpu().numpy()
                Y_tilde = predictions + (R / pi_Q_X) * (actual_label - predictions)
                pseudo_outcomes.extend(Y_tilde.tolist())
                actual_labels.extend(actual_label.tolist())
            features_collected.extend(attention_mask.cpu().numpy())

    return pseudo_outcomes, mask_collected

In [ ]:
pseudo_outcomes, features_collected = pseudo_construction(model, X_test, 0)

Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])
Shape of combined features: torch.Size([16, 774])


### Step 3: Solve the Logistic Regression Moment Equation

In [ ]:
import statsmodels.api as sm

X = sm.add_constant(features_collected)
Y_tilde = np.array(pseudo_outcomes)

model = sm.GLM(Y_tilde, X, family=sm.families.Binomial())
result = model.fit()

print(result.summary())